In [63]:
import os
import glob

import pandas as pd
import ydata_profiling

**PG&E Electric Usage by Zipcode**

Info on this dataset from PG&E (https://pge-energydatarequest.com/public_datasets/download?type=electric):

Customer usage data, both for gas (therms) and electric (kWh) usage, is reported by ZIP code, by month, by year, and by the four customer types – residential, commercial, agricultural and industrial. The reports on this data are made available pursuant to California Public Utilities Commission Decision 14-05-016 (view the Decision here). Accordingly, the public datasets meet Commission Decision rules for public aggregation of data, as follows: a minimum of 100 Residential customers; a minimum of 15 Non-Residential customers, with no single Non-Residential customer accounting for more than 15% of the total consumption. If aggregation is not met, the consumption will be combined with a neighboring ZIP code until the aggregation requirements are met.

In [28]:
df = pd.read_csv('data/PGE_ElectricUsageByZip/PGE_2013_Q1_ElectricUsageByZip.csv')

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7521 entries, 0 to 7520
Data columns (total 8 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   ZipCode         7521 non-null   int64 
 1   Month           7521 non-null   int64 
 2   Year            7521 non-null   int64 
 3   CustomerClass   7521 non-null   object
 4   Combined        7521 non-null   object
 5   TotalCustomers  7521 non-null   object
 6   TotalkWh        7521 non-null   object
 7   AveragekWh      3172 non-null   object
dtypes: int64(3), object(5)
memory usage: 470.2+ KB


In [8]:
df.head()

ZipCode  Month  Year       CustomerClass Combined TotalCustomers TotalkWh  \
0    93202      1  2013  Elec- Agricultural        Y              0        0   
1    93202      2  2013  Elec- Agricultural        Y              0        0   
2    93202      3  2013  Elec- Agricultural        Y              0        0   
3    93203      1  2013  Elec- Agricultural        Y              0        0   
4    93203      2  2013  Elec- Agricultural        Y              0        0   

  AveragekWh  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4        NaN

In [39]:
dict(zip(list(df.columns.str.upper()), list(df.columns)))

{'ZIPCODE': 'ZipCode',
 'MONTH': 'Month',
 'YEAR': 'Year',
 'CUSTOMERCLASS': 'CustomerClass',
 'COMBINED': 'Combined',
 'TOTALCUSTOMERS': 'TotalCustomers',
 'TOTALKWH': 'TotalkWh',
 'AVERAGEKWH': 'AveragekWh'}

Data comes in quarterly files. We need to concatenate them into a single DataFrame.

In [77]:
electric_usage = pd.DataFrame()

files = glob.glob('data/PGE_ElectricUsageByZip/*.csv')

colmap = {'ZIPCODE': 'ZipCode',
 'MONTH': 'Month',
 'YEAR': 'Year',
 'CUSTOMERCLASS': 'CustomerClass',
 'COMBINED': 'Combined',
 'TOTALCUSTOMERS': 'TotalCustomers',
 'TOTALKWH': 'TotalkWh',
 'AVERAGEKWH': 'AveragekWh'}

for file in files:
    df = pd.read_csv(file)
    # column names change case partway through the dataset
    df.rename(columns=colmap, inplace=True)
    electric_usage = pd.concat([electric_usage, df], ignore_index=True)

In [58]:
electric_usage.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 342338 entries, 0 to 342337
Data columns (total 8 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   ZipCode         342338 non-null  int64 
 1   Month           342338 non-null  int64 
 2   Year            342338 non-null  int64 
 3   CustomerClass   342338 non-null  object
 4   Combined        342338 non-null  object
 5   TotalCustomers  342338 non-null  object
 6   TotalkWh        342338 non-null  object
 7   AveragekWh      155236 non-null  object
dtypes: int64(3), object(5)
memory usage: 20.9+ MB


In [59]:
electric_usage.head()

ZipCode  Month  Year       CustomerClass Combined TotalCustomers TotalkWh  \
0    93101      7  2021  Elec- Agricultural        Y              0        0   
1    93101      8  2021  Elec- Agricultural        Y              0        0   
2    93101      9  2021  Elec- Agricultural        Y              0        0   
3    93110      7  2021  Elec- Agricultural        Y              0        0   
4    93110      8  2021  Elec- Agricultural        Y              0        0   

  AveragekWh  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4        NaN

In [78]:
# cast columns as appropriate data types

electric_usage['CustomerClass'] = electric_usage['CustomerClass'].astype('category')
electric_usage['Combined'] = electric_usage['Combined'].astype('category')

electric_usage['TotalCustomers'] = pd.to_numeric(electric_usage['TotalCustomers'].str.replace(',',''))
electric_usage['TotalkWh'] = pd.to_numeric(electric_usage['TotalkWh'].str.replace(',',''))
electric_usage['AveragekWh'] = pd.to_numeric(electric_usage['AveragekWh'].str.replace(',',''))



In [79]:
electric_usage.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 342338 entries, 0 to 342337
Data columns (total 8 columns):
 #   Column          Non-Null Count   Dtype   
---  ------          --------------   -----   
 0   ZipCode         342338 non-null  int64   
 1   Month           342338 non-null  int64   
 2   Year            342338 non-null  int64   
 3   CustomerClass   342338 non-null  category
 4   Combined        342338 non-null  category
 5   TotalCustomers  342338 non-null  int64   
 6   TotalkWh        342338 non-null  int64   
 7   AveragekWh      155236 non-null  float64 
dtypes: category(2), float64(1), int64(5)
memory usage: 16.3 MB


In [62]:
electric_usage['TotalkWh'].describe()

count    3.423380e+05
mean     2.508318e+06
std      1.367032e+07
min      0.000000e+00
25%      0.000000e+00
50%      0.000000e+00
75%      1.981495e+06
max      1.250439e+09
Name: TotalkWh, dtype: float64

In [65]:
report = electric_usage.profile_report(sort=None, html={'style':{'full_width': True}}, progress_bar=False)
report

In [68]:
report_residential = electric_usage.loc[electric_usage['CustomerClass'] == 'Elec- Residential'].profile_report(sort=None, html={'style':{'full_width': True}}, progress_bar=False)
report_residential

In [69]:
report_residential.to_widgets()

In [87]:
# Explore duplicates

duplicates = electric_usage.duplicated()
sum(duplicates)

14863

In [88]:
len(electric_usage)

342338

In [85]:
electric_usage_nodup = electric_usage.drop_duplicates()

In [89]:
len(electric_usage_nodup)

327475

In [90]:
14863+327475

342338